<table style="width: 100%; border-style: none">
<tr style="border-style: none; background-color: #82a8cf">
<td style="border-style: none; width: 1%; text-align: left; font-size: 18px; color: #ffffff">Institut f&uuml;r Theoretische Physik<br /> <font color="#e6e6e6">Universit&auml;t zu K&ouml;ln </font></td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 18px; color: #ffffff">Prof. Dr. Simon Trebst<br /> <font color="#e6e6e6"> Christoph Berke </font> </td>
</tr>
</table>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h1 style="font-weight:200; text-align: center; margin: 0px; font-size: 48px; padding:0px; color: #606060">Statistische Physik </h1>
<h1 style="font-weight:light; text-align: center; margin: 10px; padding:0px; color: #606060">&Uuml;bungsblatt 6</h1>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h3 style="font-weight:400; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px; color: #606060">Wintersemester 23/24</h3>


<font size="4" color="#606060">**Website:** <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml</a></font>

<font size="4" color="#606060">**Abgabe**: <span style="color:#82a8cf"> 20.11.2023,10:00 Uhr </span> <span style="float:right;">**Besprechung**: 21.11.2023 </span></font>

<font size="4" color="#606060">**Name**: <span style="color:#82a8cf"> Bitte geben Sie Ihren Namen an.  </span> </font>

<table style="border-style: none; width: 100%; background-color: #FFFFFF"><tr style="border-style: none;">
<td style="border-style: none; width:3%; text-align: left; font-size: 25px; font-weight: 200;background-color: #FFFFFF">Aufgabe 22: Maxwellsche Geschwindigkeitsverteilung </td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 15px;background-color: #FFFFFF">[3 Bonuspunkte]</td></tr></table> 

In dieser Aufgabe sollen Sie, aufbauend auf der Simulation des zweidimensionalen Gases, demonstrieren, dass die Verteilung der Geschwindigkeiten in einem Gas durch die Maxwellsche Geschwindigkeitsverteilung (auch Maxwell-Boltzmann-Verteilung) gegeben ist. Nachfolgend finden Sie die Ihnen bereits bekannten Funktionen, die zum Erzeugen einer Anfangskonfiguration und der Simulation elastischer Stöße benötigt werden.

In [ ]:
using Random, LinearAlgebra, GLMakie, Statistics

In [ ]:
# Initialize positions and velocities of particles in a 2D box.
# x, y = Position arrays,
# vx, vy = velocity arrays,
# r = particle radius array
# v = particle velocity (abs. value)
# box = tuple with boundaries
function initialize_particles!(x, y, vx, vy, r, v, box)
    
    # extract boundaries
    xmin, xmax, ymin, ymax = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # random position with distance r to boundary
        x[i] = xmin+2*r[i] + rand() * (xmax - xmin - 4*r[i])
        y[i] = ymin+2*r[i] + rand() * (ymax - ymin - 4*r[i])
        
        # random velocity direction
        angle = rand()*2*pi
        vx[i], vy[i] = cos(angle)*v, sin(angle)*v
        
    end
    
end

# Same as above, but take account of the finite dimension of each particle. 
function initialize_particles_without_overlap!(x, y, vx, vy, r, v, box)
    
    # extract boundaries
    xmin, xmax, ymin, ymax = box
    
    # initialize each particle individually
    for i in 1:length(x)
        
        # reset counter of maximal tries
        tries, maxtries = 0, 1000
        
        # random position with distance r to boundary and no overlap to other particles
        overlapping = true
        while overlapping
            x[i] = xmin+2*r[i] + rand()*(xmax - xmin - 4*r[i])
            y[i] = ymin+2*r[i] + rand()*(ymax - ymin - 4*r[i])
            overlapping = false
            for j in 1:i-1
                if (x[i]-x[j])^2 + (y[i]-y[j])^2 < 1.01*(r[i]+r[j])^2
                    overlapping = true
                end
            end
            tries += 1
            # maybe break loop because of maximum tries
            if tries > maxtries
                @error "Could not place particle! Exceeded $(max_tries) tries"
                return
            end
        end
        
        # random velocity direction
        angle = rand()*2*pi
        vx[i], vy[i] = cos(angle)*v, sin(angle)*v
                
    end
    
end

In [ ]:
function move_particles!(x, y, vx, vy, dt, r, box)
    
    # move all particles by dt
    x .+= vx .* dt
    y .+= vy .* dt
    
    # check collision with bounding box
    for i in 1:length(x)
        # left / right
        if x[i]-r[i] < box[1]
            vx[i] *= -1
        elseif x[i]+r[i] > box[2]
            vx[i] *= -1
        end
        # up / down
        if y[i]-r[i] < box[3]
            vy[i] *= -1
        elseif y[i]+r[i] > box[4]
            vy[i] *= -1
        end
    end
    return 0
end

In [ ]:
function collide_particles!(x, y, vx, vy, m, r)
    
    # check all particle pairs (i,j) for collision
    for i in 1:length(x)
        for j in 1:i-1
            # particles i and j are too close --> collision
            if (x[i]-x[j])^2 + (y[i]-y[j])^2 < (r[i]+r[j])^2
                er = [x[j]-x[i], y[j]-y[i]]
                er = er ./ norm(er)
                vi = er[1]*vx[i] + er[2]*vy[i]
                vj = er[1]*vx[j] + er[2]*vy[j]
                vip = 2*(m[i]*vi + m[j]*vj)/(m[i]+m[j])  -  vi
                vjp = 2*(m[i]*vi + m[j]*vj)/(m[i]+m[j])  -  vj
                vx[i] = vx[i] + (vip - vi)*er[1]
                vy[i] = vy[i] + (vip - vi)*er[2]
                vx[j] = vx[j] + (vjp - vj)*er[1]
                vy[j] = vy[j] + (vjp - vj)*er[2]
            end
            
        end
    end
    
end

In [ ]:
# Maxwell-Boltzmann distribution in two dimensions.
function maxwell(v, m, beta)
    return  m * beta * v * exp(-m * v^2 * beta / 2)
end

## Jetzt sind Sie dran:
Nachfolgende Zelle erzeugt die Ihnen bereits bekannte Simulation. Zusätzlich ist jetzt auch noch die Verteilung der Geschwindigkeitsbeträge $|v|$ dargestellt. Die Anfangsbedingungen sind so gewählt, dass alle Teilchen zu Beginn dasselbe $|v|$ haben. Implementieren Sie andere Anfangsbedingungen etwa
- jedes zweite Teilchen ruht,
- zu Beginn sind die Geschwindigkeiten gleichförmig auf einem geeignet gewählten Intervall verteilt,
- ...

und überzeugen Sie sich davon, dass die Konvergenz gegen die Maxwellsche Geschwindigkeitsverteilung unabhängig von der Anfangskonfiguration erfolgt.
Stellen Sie in dem Histogram zusätzlich die erwartete Verteilung ```maxwell(v, m, beta)``` dar (siehe obige Zelle). Überlegen Sie sich, wie Sie aus dem mittleren $|v|$ das entsprechende $\beta$ berechnen können.

In [ ]:
### Simulation Parameters ###
N = 1000 # Number of particles
box = (0.0, 6, 0.0, 3) # Bounding box of simulation
radius = 0.002 # Radius of particles
v = 1.5 # Initial velocity
dt = 0.01 # Time step in update.
steps_per_frame = 10 # Number of updates before visualization is updated

### Initial conditions ###
x, y = zeros(N), zeros(N) # Arrays for positions.
vx, vy  = zeros(N), zeros(N) # Arrays for velocities
m, r = ones(N), radius * ones(N) # Arrays for masses and radii

### Initialize all particles with same |v| ###
initialize_particles_without_overlap!(x,y,vx,vy,r,v,box)

# Make the relevant arrays observables.
x, y, vx, vy = Observable(x), Observable(y), Observable(vx), Observable(vy)
vabs = @lift( sqrt.($vx.^2 + $vy.^2) ) # Observable that holds all abs. values of velocities.

### Set up animation ###
fig = Figure(resolution = (1300,600))
ax = Axis(fig[1,1:2], aspect = 1.333, spinewidth = 3, backgroundcolor = :gray70)
ax2 = Axis(fig[1,3:4], aspect = 1.333, xlabel = L"v", ylabel = L"p(v)")
hist!(ax2, vabs, normalization = :pdf, bins = range(0,3*v,length = 30))

limits!(ax, box[1], box[2], box[3], box[4])
hidedecorations!(ax)
scatter!(ax, x, y, color = vabs, colormap = :curl, markersize = 4500 * r, colorrange = (0, 3*v))
display(fig)

### Start/Stop Button ###
run = Button(fig[2,1]; label = "Start / Stop", tellwidth = false, tellheight = true)
isrunning = Observable(false)
on(run.clicks) do clicks; isrunning[] = !isrunning[]; end

# Restart Button
restart = Button(fig[2,2]; label = "Restart", tellwidth = false, tellheight = true)
on(restart.clicks) do _
    initialize_particles_without_overlap!(x[],y[],vx[],vy[],r,v,box)
    notify(x);notify(y);notify(vx);notify(vy)
end

### Link Button to Simulation ###
on(run.clicks) do _
    @async while isrunning[]
        isopen(fig.scene) || break # Stoppen wenn Fenster geschlossen ist.
        for j in 1:steps_per_frame
            # let particles collide with each other
            collide_particles!(x[],y[],vx[],vy[],m,r)
            # let particles move
            move_particles!(x[],y[],vx[],vy[],dt/steps_per_frame,r,box)
        end

        notify(x);notify(y);notify(vx);notify(vy)
        sleep(0.01)
    end 
end